In [1]:
import os
import re
earlygreekepic = ['tlg0012','tlg0020','tlg0013']

def addentry(curdict,curitem):
    if(curitem in curdict):
        curdict[curitem] = curdict[curitem] + 1
    else:
        curdict[curitem] = 1

def getepicfiles():
    rlist = []
    for (root,dirs,files) in os.walk('.'):
        m = re.search('(tlg[0-9]+)',root)
        if(not m):
            continue
        if(m and not m[1] in earlygreekepic):
            continue
        for file in files:
            if(re.search('tlg0012.tlg00[12].daphne_tb',file)):
                continue
            if(re.search('tlg0020.tlg00[123].daphne_tb',file)):
                continue
            if(re.search('\.bak',file)):
                continue
            if(re.search('conllu$',file)):
                #print(root,file)
                rlist.append(root+'/'+file)
    return(rlist)

flist = getepicfiles()
flist

['./tlg0020/tlg0020.tlg002.daphne_perstb-grc1.conllu',
 './tlg0020/tlg0020.tlg003.daphne_perstb-grc1.conllu',
 './tlg0020/tlg0020.tlg001.daphne_perstb-grc1.conllu',
 './tlg0012/tlg001/tlg0012.tlg001.daphne_perstb-grc1.1-6.conllu',
 './tlg0012/tlg001/tlg0012.tlg001.daphne_perstb-grc1.7-12.conllu',
 './tlg0012/tlg001/tlg0012.tlg001.daphne_perstb-grc1.13-18.conllu',
 './tlg0012/tlg001/tlg0012.tlg001.daphne_perstb-grc1.19-24.conllu',
 './tlg0012/tlg002/tlg0012.tlg002.daphne_perstb-grc1.7-12.conllu',
 './tlg0012/tlg002/tlg0012.tlg002.daphne_perstb-grc1.19-24.conllu',
 './tlg0012/tlg002/tlg0012.tlg002.daphne_perstb-grc1.1-6.conllu',
 './tlg0012/tlg002/tlg0012.tlg002.daphne_perstb-grc1.13-18.conllu',
 './tlg0013/tlg0013.tlg002.daphne_tb-grc1.conllu']

In [2]:
wordid2cit = {}
wordid2form= {}
wordid2lemma = {}
wordid2upos = {}
wordid2xpos = {}
wordid2feats = {}
wordid2head = {}
wordid2deprel = {}
wordid2deplist = {}
lemmaindex = {}
formindex = {}
verbargs = {}
worddeprels = {}


def additem(curdict,curitem):
    if(curitem in curdict):
        curdict[curitem] = curdict[curitem] + 1
    else:
        curdict[curitem] = 1

def add2lemmaindex(lemmaindex,lemma,wordid):
    if(not lemma in lemmaindex):
        lemmaindex[lemma] = [wordid]
    else:
        lemmaindex[lemma].append(wordid)

def add2formindex(formindex,curform,wordid):
    if(not curform in formindex):
        formindex[curform] = [wordid]
    else:
        formindex[curform].append(wordid)

def loadUDfile(fname):
    cursentid = ''
    m = re.search('(tlg[0-9]+\.tlg[0-9]+)',fname)
    if(not m):
        print(fname,'expected file name with tlg[0-9]+\.tlg[0-9]+')
        return

    else:
        curtgwork = m[1]
    f = open(fname)
    for l in f:
        l = re.sub('\s+$','',l)
        if(re.search('u--------',l)):
            continue
        curcit = ''
        m = re.search('sent_id\s*=\s*([0-9a-b]+)',l)
        if(m):
            cursentid = m[1]
        m = re.search('^([0-9]+)\s',l)
        if(not m):
            continue
        args = l.split()
            
        wordid = curtgwork + ':sent-' + cursentid + ':' + m[1]
        m = re.search('Ref=([^\|]+)',l)
        if(m):
            curcit = curtgwork + ':' + m[1]
        wordid2cit[wordid] = curcit
        args = l.split()
        #print(len(args),l)
        wordid2form[wordid] = args[1]
        add2formindex(formindex,args[1],wordid)
        wordid2lemma[wordid] = args[2]
        add2lemmaindex(lemmaindex,args[2],wordid)
        wordid2upos[wordid] = args[3]
        wordid2xpos[wordid] = args[4]
        wordid2feats[wordid] = args[5]
        wordid2head[wordid] = curtgwork + ':sent-' + cursentid + ':' + args[6]
            
        wordid2deprel[wordid] = args[7]
    f.close()

saveconjs = {}
def resolveconj():
    for wordid in wordid2deprel:
        if(wordid2lemma[wordid] == 'μῆνις'):
            print('1',wordid)
        #print('2',wordid,wordid2lemma[wordid])
        if(wordid2deprel[wordid] == 'conj'):
            curlemma = wordid2lemma[wordid]
            if(not curlemma in saveconjs):
                saveconjs[curlemma] = {}
            additem(saveconjs[curlemma],wordid+':'+wordid2lemma[wordid] + ':' + wordid2head[wordid] + ':'  + wordid2lemma[wordid2head[wordid]])
            wordid2deprel[wordid] = wordid2deprel[wordid2head[wordid]]
            wordid2head[wordid] = wordid2head[wordid2head[wordid]]
        if(not wordid2head[wordid] in wordid2deplist):
            wordid2deplist[wordid2head[wordid]] = [wordid]
        else:
            wordid2deplist[wordid2head[wordid]].append(wordid)
        if(not wordid in wordid2lemma):
            print('missing lemma',wordid)
            continue
        if(not wordid2lemma[wordid] in worddeprels):
            worddeprels[wordid2lemma[wordid]] = {}
        if(wordid2lemma[wordid] == 'μῆνις'):
            print(wordid,wordid2lemma[wordid],worddeprels[wordid2lemma[wordid]])
        additem(worddeprels[wordid2lemma[wordid]],wordid2deprel[wordid])

        
        


lemmadeps = {}
def getdeps(lemma):
    rlist = {}
    if(not lemma in lemmaindex):
        return

    print(lemma,len(lemmaindex[lemma]))
    for wordid in lemmaindex[lemma]:
        if(not wordid in wordid2deplist):
            continue
        print('\n'+wordid,wordid2lemma[wordid],wordid2form[wordid])
        for depid in wordid2deplist[wordid]:
            if(not lemma in verbargs):
                verbargs[lemma] = {}
            
            additem(verbargs[lemma],wordid2lemma[depid]+ ':' + wordid2deprel[depid])
            print(depid,wordid2form[depid],wordid2lemma[depid],wordid2deprel[depid])
            
            
for fname in flist:   
    loadUDfile(fname)
resolveconj()




curlemma = 'συνάγω'
getdeps(curlemma)
for foo in sorted(verbargs[curlemma],key=verbargs[curlemma].get,reverse=True):
    print(foo,verbargs[curlemma][foo])


1 tlg0020.tlg003:sent-2273422:5
tlg0020.tlg003:sent-2273422:5 μῆνις {}
1 tlg0012.tlg001:sent-2274106:1
tlg0012.tlg001:sent-2274106:1 μῆνις {'obj': 1}
1 tlg0012.tlg001:sent-2274140:8
tlg0012.tlg001:sent-2274140:8 μῆνις {'obj': 2}
1 tlg0012.tlg001:sent-2275445:29
tlg0012.tlg001:sent-2275445:29 μῆνις {'obj': 3}
1 tlg0012.tlg001:sent-2275520:5
tlg0012.tlg001:sent-2275520:5 μῆνις {'obj': 4}
1 tlg0012.tlg001:sent-2275665:9
tlg0012.tlg001:sent-2275665:9 μῆνις {'obj': 4, 'nsubj': 1}
1 tlg0012.tlg001:sent-2277013:22
tlg0012.tlg001:sent-2277013:22 μῆνις {'obj': 5, 'nsubj': 1}
1 tlg0012.tlg001:sent-2278452:35
tlg0012.tlg001:sent-2278452:35 μῆνις {'obj': 6, 'nsubj': 1}
1 tlg0012.tlg001:sent-2278897:14
tlg0012.tlg001:sent-2278897:14 μῆνις {'obj': 7, 'nsubj': 1}
1 tlg0012.tlg001:sent-2279597:9
tlg0012.tlg001:sent-2279597:9 μῆνις {'obj': 7, 'nsubj': 1, 'amod': 1}
1 tlg0012.tlg001:sent-2280451:9
tlg0012.tlg001:sent-2280451:9 μῆνις {'obj': 8, 'nsubj': 1, 'amod': 1}
1 tlg0012.tlg001:sent-2280470:9
tlg00

In [3]:
formindex['ἴδιον']

['tlg0012.tlg002:sent-2191172:1', 'tlg0012.tlg002:sent-2186444:3']

In [4]:
lemmacounts = {}

for curlemma in lemmaindex:
    lemmacounts[curlemma] = len(lemmaindex[curlemma])

def getverbs(getvoice):
    curvoice = ''
    curdeprel = ''
    for wordid in wordid2lemma:
        curlemma = wordid2lemma[wordid]
        m = re.search('Voice=(Act|MidPass|Mid|Pass)',wordid2feats[wordid])
        if(not m):
            continue
        curvoice = m[1]
        #print('feats',wordid,wordid2lemma[wordid],wordid2feats[wordid])
        if(not wordid in wordid2deplist):
            continue
        curobjs = []
        curcase = ''
        if(not curlemma in verbobjsindex):
            verbobjsindex[curlemma] = {}
        if(not wordid2lemma[wordid] in activeverbobjs):
            activeverbobjs[wordid2lemma[wordid]] = {}
        for wordid2 in wordid2deplist[wordid]:
            #print('feats',wordid,wordid2lemma[wordid],wordid2feats[wordid],wordid2,wordid2deprel[wordid2])
            m = re.search('\\b(obj|iobj|ccomp)',wordid2deprel[wordid2])
            if(m):
                curdeprel = m[1]
                m = re.search('Case=([A-Za-z]+)',wordid2feats[wordid2])
                if(m):
                    curcase = m[1]
                else:
                    curcase = 'nocase'
                curkey = curvoice + ':' + curdeprel + ':' + curcase + ':' + wordid2lemma[wordid2]
                
                if(not curkey in verbobjsindex[curlemma]):
                    verbobjsindex[curlemma][curkey] = [wordid + ':' + wordid2]
                else:
                    verbobjsindex[curlemma][curkey].append(wordid + ':' + wordid2)
                curobjs.append(wordid2)
                addentry(activeverbobjs[wordid2lemma[wordid]],curkey)
                #print('actobj',wordid,wordid2lemma[wordid],wordid2lemma[wordid2])
        if(not curobjs):
            curkey = curvoice+':'+'noobj'+':NA'
            curobjs.append(curkey)
            if(not curkey in verbobjsindex[curlemma]):
                verbobjsindex[curlemma][curkey] = [wordid + ':' + wordid2]
            else:
                verbobjsindex[curlemma][curkey].append(wordid + ':' + wordid2)
            addentry(activeverbobjs[wordid2lemma[wordid]],curvoice+':'+'noobj'+':NA')
            #print('noaccobj',wordid,wordid2lemma[wordid])
        #if(len(curobjs)>1):
         #   print('mult',len(curobjs),wordid,curobjs)

activeverbobjs = {}
mpverbobjs = {}
verbobjsindex = {}
                
getverbs("active")
verbobjsindex

{'κλείω': {'Act:noobj:NA': ['tlg0020.tlg002:sent-1715891:4:tlg0020.tlg002:sent-1715891:3'],
  'Act:obj:Acc:εἰμί': ['tlg0020.tlg001:sent-2273677:8:tlg0020.tlg001:sent-2273677:11',
   'tlg0020.tlg001:sent-2273677:8:tlg0020.tlg001:sent-2273677:14'],
  'Act:obj:Acc:ἦθος': ['tlg0020.tlg001:sent-2273692:15:tlg0020.tlg001:sent-2273692:12'],
  'Act:obj:Acc:γένος': ['tlg0020.tlg001:sent-2273712:1:tlg0020.tlg001:sent-2273712:5'],
  'Act:obj:nocase:ὁ': ['tlg0012.tlg002:sent-2185714:19:tlg0012.tlg002:sent-2185714:17'],
  'Act:obj:Acc:σύ': ['tlg0012.tlg002:sent-2190319:5:tlg0012.tlg002:sent-2190319:4']},
 'ἐνέπω': {'Act:obj:Acc:Ζεύς': ['tlg0020.tlg002:sent-1715891:8:tlg0020.tlg002:sent-1715891:7'],
  'Act:obj:Dat:μῦθος': ['tlg0020.tlg002:sent-1716001:10:tlg0020.tlg002:sent-1716001:8'],
  'Act:noobj:NA': ['tlg0020.tlg002:sent-1716045:35:tlg0020.tlg002:sent-1716045:34',
   'tlg0012.tlg001:sent-2277790:13:tlg0012.tlg001:sent-2277790:12',
   'tlg0012.tlg002:sent-2191971:14:tlg0012.tlg002:sent-2191971:1

In [5]:
print(len(activeverbobjs))
for curlemma in sorted(lemmacounts,key=lemmacounts.get,reverse=True):
    if(not curlemma in activeverbobjs):
        continue
    curdict = activeverbobjs[curlemma]
    formcnt = 0
    for foo in curdict:
        formcnt = formcnt + curdict[foo]
    print('\nlemma:'+curlemma,lemmacounts[curlemma],len(curdict))
    for boo in sorted(curdict,key=curdict.get,reverse=True):
        print(boo,curdict[boo])
    
activeverbobjs

2542

lemma:εἰμί 2299 37
Act:noobj:NA 593
Mid:noobj:NA 52
Act:obj:Dat:ἐγώ 13
Act:iobj:Dat:ἐγώ 11
Act:obj:Dat:ἕ 10
Act:obj:Dat:σύ 8
MidPass:noobj:NA 7
Mid:obj:Dat:σύ 3
Pass:noobj:NA 3
Act:obj:Dat:ὅς 3
Act:obj:Gen:ἄλλος 2
Mid:obj:Dat:ὁ 2
Act:obj:Gen:θεός 2
Act:obj:Dat:πούς 2
Act:obj:Dat:Μενέλαος 1
Act:obj:Gen:ἄνθρωπος 1
Act:obj:Dat:Κουρῆτες 1
Act:obj:Acc:ἔργον 1
Act:obj:Acc:ὅς 1
Act:obj:nocase:κλισίηθεν 1
Act:obj:Gen:ἀνήρ 1
Act:obj:Dat:ὁ 1
Act:obj:Dat:Φαίαξ 1
Act:obj:Dat:εἰμί 1
Act:ccomp:nocase:ἔχω 1
Act:ccomp:nocase:ἀκουάζομαι 1
Act:ccomp:nocase:φορέω 1
Act:ccomp:nocase:ἐγχέω 1
Act:obj:Acc:φάος:φόως 1
Act:obj:Dat:αὐτός 1
Act:obj:Acc:νόος 1
Act:obj:Gen:βροτός 1
Act:obj:Gen:Ἄργος 1
Act:obj:nocase:ἐνθάδε 1
Act:obj:Gen:πόλις 1
Act:obj:nocase:ξυνεείκοσι 1
Act:obj:Dat:βροτός 1

lemma:ἔχω 887 447
Act:noobj:NA 67
Act:obj:Acc:θυμός 34
Act:obj:Acc:δῶμα 25
Act:obj:Acc:ἵππος 24
Act:obj:Acc:ἔγχος 22
Act:obj:Acc:οὐρανός 22
Mid:noobj:NA 17
Act:obj:Acc:ἐγώ 16
Act:obj:Acc:Ὄλυμπος 15
Act:obj:Acc:ὁ 15
Act

Act:obj:nocase:ἐξαίρω 1
Act:obj:Acc:πέλεκυς 1
Act:obj:Acc:σκέπαρνον 1
Act:obj:Acc:κρήδεμνον 1
Act:ccomp:nocase:εἴδω:εἶδον 1
Act:obj:Acc:ἐπιφροσύνη 1
Act:obj:Acc:ῥάκος 1
Act:obj:Acc:πόσις1:πόσις 1
Act:obj:Acc:πόσις2:πόσις 1
Act:obj:Acc:λέβης 1
Act:obj:Acc:πήρα 1
Act:obj:Acc:στοναχή 1
Act:iobj:Dat:οἰκεύς 1
Act:obj:Acc:σκύφος 1
Act:obj:Acc:παῦρος 1
Act:obj:Acc:ῥηξηνορία 1
Act:iobj:Dat:ἄλοχος 1
Act:obj:nocase:Σάμη 1
Act:obj:Dat:αἰδοῖος 1
Act:obj:Acc:ἐπίβαθρον 1
Act:obj:Acc:ἱερός 1
Act:obj:Acc:πύρνον 1
Act:obj:Acc:κοτύλη 1
Act:obj:Acc:οὗτος 1
Act:obj:Dat:ἄλλος 1
Act:obj:Acc:λωίων 1
Act:iobj:Dat:ἐπιστάτης 1
Act:obj:Acc:ἅλς1:ἅλς 1
Act:ccomp:nocase:πέλω 1
Act:obj:Acc:ἄθυρμα 1
Act:iobj:Dat:Ἅιδης 1
Act:obj:Acc:ἀνήρ 1
Act:obj:Acc:μίγνυμι 1
Act:obj:Acc:κόκκος 1

lemma:βάλλω 483 250
Act:noobj:NA 72
MidPass:noobj:NA 37
Act:obj:Acc:ὁ 34
Act:obj:Acc:μιν 14
Act:obj:Acc:χείρ 10
Mid:iobj:Dat:ὦμος 9
Act:obj:Acc:χλαῖνα 9
Act:obj:Acc:χιτών 9
Act:obj:Acc:ἐγώ 8
Act:obj:Acc:ὅς 8
Act:obj:Acc:σύ 8
Mid:obj:Acc:ξί

Act:obj:nocase:οὐρανόθεν 1
MidPass:obj:Acc:νεκρός 1
Act:obj:Acc:ὄνειαρ 1
Act:obj:Acc:πῆμα 1
Act:obj:Acc:κῆρυξ 1
Act:obj:Acc:δόμος 1
Act:obj:nocase:Τροίανδε 1
Act:obj:Acc:ξύλον 1
Act:obj:nocase:Ἀπείρηθεν 1
Act:obj:Acc:Ῥαδάμανθυς 1
MidPass:obj:Acc:χρυσός 1
MidPass:obj:Acc:κειμήλιον 1
Mid:obj:nocase:οἴκαδε 1
Mid:obj:Acc:ἐγώ 1
Act:obj:Acc:τιμή 1
Act:obj:Dat:σύ 1
Act:obj:Acc:Μελάνθιος 1
Act:obj:nocase:οἶκόνδε 1
Act:obj:Acc:ἠώς 1
Act:obj:Acc:Ὀδυσσεύς 1
Act:obj:Acc:σίδηρος 1
Act:obj:Acc:ἀμύντωρ 1
Act:obj:Acc:κτῆμα 1
Act:obj:Gen:κέρας 1
MidPass:iobj:Dat:υἱός 1
MidPass:obj:nocase:Σπάρτηθεν 1
MidPass:obj:Acc:κόρη 1
Act:obj:Acc:αὐτός 1
Mid:noobj:NA 1
Act:obj:Acc:φρόνις 1
Act:obj:Acc:νῶτον 1
Act:obj:nocase:ἔνθα 1
Mid:obj:Acc:ἵππος 1
Act:obj:Acc:μῆλον1:μῆλον 1
Act:obj:Acc:κλέος 1
Act:obj:Acc:ζῶστρον 1
Act:obj:Acc:πέπλος 1
Act:obj:Acc:ῥῆγος 1
MidPass:obj:Acc:εἷμα 1
MidPass:obj:nocase:οἶκόνδε 1
Act:obj:Acc:ὗς 1
Act:obj:Acc:φόρτος 1
Act:obj:Acc:χρῆμα 1
Act:iobj:Dat:ἐγώ 1
Act:obj:Acc:ἄριστος 1
Act:obj:

Act:iobj:Dat:θεός 1
Act:obj:Acc:κολῳός 1
Act:obj:Acc:κακός 1
Act:obj:Acc:Ὑψήνωρ 1
Act:obj:Acc:κόρση 1
Act:obj:Acc:Ἀχαιός 1
Act:obj:Acc:πόντος 1
Mid:obj:Acc:ἵππος 1
Act:obj:Acc:ὄγμος 1
Act:obj:Acc:Ἄντιφος 1
Act:obj:nocase:σχεδόν 1
MidPass:obj:Acc:ῥύσιον 1
Mid:obj:Acc:ὁ 1
Act:obj:Acc:ὅς 1
Act:obj:Acc:Δηίπυρος 1
Act:obj:Acc:δίκη 1
MidPass:obj:Dat:ὀδύνη 1
Act:obj:Acc:ἕρκος 1
Act:obj:Acc:Τρώς 1
Act:obj:nocase:ἅδην 1
Act:iobj:Dat:σάκος 1
Act:obj:Acc:ἔγχος 1
Act:obj:Acc:πτύξ 1
Act:obj:Acc:Ἔχεκλος 1
Act:obj:Dat:στῆθος 1
Act:obj:nocase:τῇ 1
Act:obj:Acc:Ἀρίων 1
Act:obj:Acc:ἕ 1
Act:iobj:Dat:πόντος 1
Act:obj:Acc:γαλήνη 1
Act:obj:Acc:μοχλός 1
Act:obj:Acc:σύ 1
Mid:obj:Acc:βοῦς 1
Mid:obj:Acc:μῆλον1:μῆλον 1
Act:obj:Gen:πρόθυρον 1
Act:obj:Gen:αἴθουσα 1
Act:obj:Acc:πέτρα 1
Act:obj:Acc:αὐτός 1
Act:obj:Acc:τεῖχος 1
Act:iobj:Dat:πόλις 1
MidPass:obj:nocase:οἴκαδε 1
Act:obj:Acc:σταυρός 1
Act:obj:Acc:κάρα 1
Act:obj:Acc:ὦμος 1
Act:obj:Acc:ὀδών 1

lemma:εἶδον 178 77
Act:noobj:NA 48
Act:obj:Acc:ὁ 16
Mid:noobj:NA

Act:ccomp:nocase:κλονέω 1
Act:obj:Acc:ἑταῖρος 1
Act:obj:Acc:νίκη 1
Act:obj:Acc:Σαρπηδών 1
Act:obj:Acc:τάλαντον 1
Act:obj:Acc:Ἀπόλλων 1
Act:obj:Gen:Ἀχαιός 1
Act:ccomp:nocase:ἀρήγω 1
Act:ccomp:nocase:κυλίνδω 1
Act:ccomp:Gen:Τρώς 1
Act:ccomp:nocase:παύω 1
Mid:obj:Acc:αὐτός 1
Act:obj:Acc:μῦθος 1
Act:obj:Acc:βουλή 1
Act:ccomp:nocase:φοβέω 1
Act:ccomp:nocase:φεύγω 1
Act:ccomp:nocase:θνῄσκω 1
Mid:obj:Acc:ἵππος 1
Act:obj:Nom:ὑπερφίαλος 1
Act:obj:Nom:ἀπηνής 1
Mid:noobj:NA 1
Act:obj:Acc:φᾶρος 1
Act:obj:Acc:χιτών 1
Act:ccomp:nocase:πέλω 1
Act:obj:Acc:οὐλή 1
Act:ccomp:nocase:ἵκω 1
Act:obj:Gen:ἀλλήλων 1
Act:ccomp:nocase:ἱκάνω 1
Act:obj:Nom:ἀμείνων 1
Act:obj:Acc:πᾶς 1
Mid:obj:Gen:ἀλλήλων 1
Act:obj:Acc:παῖς 1
Act:obj:Acc:ὄρνις 1
Act:obj:Acc:τοιοῦτος 1
Act:obj:Acc:ἰθύς 1
Mid:obj:Acc:θυμός 1
Act:obj:Acc:ἕ 1
Act:ccomp:nocase:τίθημι 1
Act:ccomp:Nom:ἐναίσιμος 1
Act:ccomp:Nom:ἀθέμιστος 1
Act:obj:Acc:αὐτός 1

lemma:οἴομαι 129 90
Act:ccomp:nocase:τελέω 6
Act:ccomp:nocase:πείθω 4
MidPass:noobj:NA 4
MidPass:cc

...

Mid:obj:Acc:ὁ 1
Mid:obj:Acc:κόρη 1
Mid:obj:Acc:παῖς 1
Mid:obj:Acc:μιν 1

lemma:γεύω 5 5
Mid:obj:Gen:ἀλλήλων 1
Mid:obj:Gen:ἀκωκή 1
Mid:obj:Gen:χείρ 1
Mid:obj:Gen:ὀιστός 1
Mid:obj:Gen:προίξ 1

lemma:τίλλω 5 6
Act:noobj:NA 1
Act:obj:Acc:κόμη 1
MidPass:obj:Acc:ὁ 1
MidPass:obj:Acc:χαίτη 1
Act:iobj:Dat:πούς 1
Act:obj:Acc:πέλεια 1

lemma:προτιόσσομαι 5 5
MidPass:obj:Acc:τις 2
MidPass:noobj:NA 1
MidPass:obj:Acc:ὄλεθρος 1
MidPass:iobj:Dat:ἐγώ 1
MidPass:obj:Acc:θάνατος 1

lemma:δορπέω 5 1
Act:noobj:NA 5

lemma:καταδαρθάνω 5 1
Act:noobj:NA 5

lemma:ἀλεγύνω 5 3
Act:obj:Acc:δαίς1:δαίς 3
Act:obj:Acc:ὅς 1
Act:obj:Acc:δαίς1:δαίτη 1

lemma:κεράω 5 2
MidPass:obj:Acc:οἶνος 4
Act:obj:Acc:οἶνος 1

lemma:εἴρω 5 5
MidPass:obj:Dat:ἤλεκτρον 2
MidPass:obj:Acc:ὅστις 1
MidPass:obj:Acc:σύ 1
MidPass:noobj:NA 1
MidPass:ccomp:nocase:μυθέομαι 1

lemma:κέλλω 5 2
Act:obj:Acc:ναῦς 3
Act:iobj:Dat:ψάμαθος 2

lemma:ἐκπίνω 5 3
Act:noobj:NA 4
MidPass:obj:Acc:ὅσος 1
MidPass:iobj:Dat:σύ 1

lemma:ἐρωτάω 5 5
Act:obj:Acc:ἐγώ 4
Act

lemma:ἐμπλήσσω 3 3
Act:obj:Dat:τάφρος 2
Act:obj:Dat:σκόλοψ 1
Act:obj:Dat:ἕρκος 1

lemma:προβιβάω 3 1
Act:noobj:NA 2

lemma:κραδαίνω 3 1
MidPass:noobj:NA 1

lemma:λάω 3 3
MidPass:obj:Acc:Ἀδάμας 1
Act:obj:Acc:ἀσπαίρω 1
Act:obj:Acc:νεβρός 1

lemma:βιβάσθω 3 1
Act:noobj:NA 3

lemma:προθρώσκω 3 1
Act:noobj:NA 1

lemma:πηδάω 3 2
Act:obj:nocase:ὑψόσε 2
Act:noobj:NA 1

lemma:ἀπινύσσω 3 1
Act:noobj:NA 3

lemma:διαπέταμαι 3 1
Mid:noobj:NA 2

lemma:δεικανάω 3 1
MidPass:noobj:NA 3

lemma:εἰσαγείρω 3 2
MidPass:obj:Acc:θυμός 2
Mid:noobj:NA 1

lemma:εἰσελαύνω 3 2
Act:obj:Acc:ἵππος 1
Act:noobj:NA 1

lemma:ἐνθρώσκω 3 3
Act:obj:Dat:ὅμιλος 1
Act:obj:Dat:μέσος 1
Act:obj:Dat:πόντος 1

lemma:διίημι 3 4
Mid:noobj:NA 1
Mid:obj:Acc:μάχη 1
Mid:obj:Acc:ἐνοπή 1
Mid:obj:Acc:ξένος 1

lemma:προσδέρκομαι 3 3
MidPass:obj:Acc:μιν 1
MidPass:obj:Acc:πατήρ 1
MidPass:obj:Acc:ἀοιδός 1

lemma:προτεύχω 3 1
MidPass:noobj:NA 2

lemma:ἀνθίστημι 3 3
MidPass:noobj:NA 1
Act:obj:Dat:Ἥρα 1
Act:obj:Dat:Λητώ 1

lemma:ἐπιχράω 3 4
Act:ob

Act:noobj:NA 2

lemma:ἐμπίτνω 2 2
Act:noobj:NA 1
Act:obj:Dat:ἕ 1

lemma:ἀνόρουω 2 1
Act:noobj:NA 2

lemma:ερχομαι 2 2
Act:obj:Dat:ἐγώ 1
Act:obj:Dat:ὁ 1

lemma:πλάσσω 1 1
Act:obj:Acc:ἴκελος 1

lemma:ἐκπέτομαι 1 1
Act:noobj:NA 1

lemma:ἐπιλαμβάνω 1 1
Act:noobj:NA 1

lemma:ἐκκορυφόω 1 1
Act:obj:Acc:λόγος 1

lemma:μέμφομαι 1 1
Mid:obj:Acc:ὁ 1

lemma:στέρομαι 1 1
MidPass:obj:Gen:νίκη 1

lemma:παρεκβαίνω 1 1
Act:obj:Gen:δίκαιος 1

lemma:καταβρίθω 1 1
Act:obj:Dat:μαλλός 1

lemma:καταφράζω 1 1
MidPass:obj:Acc:δίκη 1

lemma:ὀνοτάζω 1 1
Act:noobj:NA 1

lemma:κατοπάζω 1 1
Act:obj:Acc:αἰδώς 1

lemma:ὠνέομαι 1 1
MidPass:obj:Acc:κλῆρος 1

lemma:κερδαίνω 1 1
Act:obj:Acc:κακός 1

lemma:κωτίλλω 1 1
Act:obj:Acc:αἱμύλος 1

lemma:φέρβω 1 1
Act:obj:Acc:οἶκος 1

lemma:ἐγκαταλείπω 1 1
Act:obj:Acc:παῖς 1

lemma:βοωτέω 1 1
Act:noobj:NA 1

lemma:ἐπιμετρέω 1 1
Act:noobj:NA 1

lemma:διατεκμαίρομαι 1 2
Mid:obj:Acc:ὁ 1
Mid:iobj:Dat:ἄνθρωπος 1

lemma:ζητεύω 1 1
Act:obj:Acc:βίοτος 1

lemma:λυπέω 1 1
Act:noobj:NA 1

l

lemma:λευκαίνω 1 1
Act:obj:Acc:ὕδωρ 1

lemma:ἐξορμάω 1 1
Act:obj:nocase:ἐκεῖσε 1

lemma:ἀναμορμύρω 1 1
Act:noobj:NA 1

lemma:ἀδέω:ἁνδάνω 1 2
Act:obj:Dat:κάματος 1
Act:obj:Dat:ὕπνος 1

lemma:ἐξαποβαίνω 1 1
Act:obj:Gen:ναῦς 1

lemma:εἰσερύω 1 1
Act:obj:Acc:σπέος 1

lemma:ἐποπτάω 1 1
Act:obj:Acc:ἔγκατα 1

lemma:ἐκτείνω 1 1
Act:obj:Acc:βοῦς 1

lemma:ἀναμετρέω 1 1
Act:obj:Acc:Χάρυβδις 1

lemma:κατασκιάω 1 1
Act:obj:Acc:Χάρυβδις 1

lemma:ἀναμάσσω 1 1
Act:obj:Acc:ὅς 1

lemma:δακρυπλώω 1 1
Act:noobj:NA 1

lemma:ἀγυρτάζω 1 1
Act:obj:Acc:χρῆμα 1

lemma:θαλπιάω 1 1
Act:noobj:NA 1

lemma:ἀναμένω 1 1
Act:obj:Acc:ἠώς 1

lemma:καθεψιάομαι 1 1
MidPass:obj:Gen:σύ 1

lemma:ἐξαπονίζω 1 1
Act:obj:Acc:πούς 1

lemma:ἐπαφύσσω 1 1
Act:noobj:NA 1

lemma:καναχέω 1 1
Act:noobj:NA 1

lemma:διαρρίπτω 1 1
Act:obj:Acc:ὀιστός 1

lemma:παρήμαι 1 1
MidPass:noobj:NA 1

lemma:προσστείχω 1 1
Act:obj:Acc:Ὄλυμπος 1

lemma:ἀλέω:ἀλέομαι 1 1
Act:obj:Acc:πυρός 1

lemma:ὑποστορέννυμι 1 1
Act:obj:Acc:δέμνιον 1

lemma:δαρθάνω 1 1


{'κλείω': {'Act:noobj:NA': 1,
  'Act:obj:Acc:εἰμί': 2,
  'Act:obj:Acc:ἦθος': 1,
  'Act:obj:Acc:γένος': 1,
  'Act:obj:nocase:ὁ': 1,
  'Act:obj:Acc:σύ': 1},
 'ἐνέπω': {'Act:obj:Acc:Ζεύς': 1,
  'Act:obj:Dat:μῦθος': 1,
  'Act:noobj:NA': 4,
  'Act:obj:Acc:ὄνομα': 1,
  'Act:obj:Acc:ὄνειρος': 1,
  'Act:ccomp:Nom:ἄριστος': 1,
  'Act:iobj:Dat:ἐγώ': 11,
  'Act:obj:Dat:σφεῖς': 1,
  'Act:iobj:Dat:Ἀχιλλεύς': 1,
  'Act:obj:Acc:μῦθος': 3,
  'Act:obj:Acc:μῆτις': 1,
  'Act:ccomp:Nom:ἄξιος': 1,
  'Act:obj:Acc:οἶτος': 1,
  'Act:obj:Dat:φίλος': 2,
  'Act:ccomp:nocase:περιγίγνομαι': 2,
  'Act:iobj:Dat:σύ': 2,
  'Act:obj:Acc:νόστος': 1,
  'Act:obj:Acc:οὗτος': 1,
  'Act:obj:Dat:ἐγώ': 4,
  'Act:ccomp:nocase:ἀποκτείνω': 1,
  'Act:ccomp:nocase:ἄγω': 1,
  'Act:obj:Acc:θάνατος': 1,
  'Act:obj:Acc:κήρ': 1,
  'Act:obj:Acc:ἀνήρ': 1,
  'Act:obj:Acc:ὄλεθρος': 2,
  'Act:obj:Acc:νημερτής': 5,
  'Act:obj:Acc:ἀληθής': 1,
  'Act:obj:Acc:ὅδε': 1,
  'Act:obj:Acc:κληδών': 1,
  'Act:ccomp:nocase:οἴχομαι': 1,
  'Act:ccomp:nocas

In [5]:
verbobjsindex['εἶπον']['Act:ccomp:nocase:κελεύω']


['tlg0020.tlg001:sent-2273935:12:tlg0020.tlg001:sent-2273935:19',
 'tlg0012.tlg001:sent-2276230:8:tlg0012.tlg001:sent-2276230:14',
 'tlg0012.tlg001:sent-2276377:10:tlg0012.tlg001:sent-2276377:16',
 'tlg0012.tlg001:sent-2276391:10:tlg0012.tlg001:sent-2276391:16',
 'tlg0012.tlg001:sent-2276458:11:tlg0012.tlg001:sent-2276458:17',
 'tlg0012.tlg002:sent-2187315:9:tlg0012.tlg002:sent-2187315:15',
 'tlg0012.tlg002:sent-2187410:10:tlg0012.tlg002:sent-2187410:16',
 'tlg0012.tlg002:sent-2191392:1:tlg0012.tlg002:sent-2191392:7',
 'tlg0012.tlg002:sent-2191439:2:tlg0012.tlg002:sent-2191439:8',
 'tlg0012.tlg002:sent-2190349:10:tlg0012.tlg002:sent-2190349:16',
 'tlg0012.tlg002:sent-2190658:10:tlg0012.tlg002:sent-2190658:16']

In [7]:
curlem = 'πέμπω'
for foo in sorted(verbargs[curlem],key=verbargs[curlem].get,reverse=True):
    print(foo,verbargs[curlem][foo])

KeyError: 'πέμπω'

In [8]:
curlemma = 'χόλος'
curlemma = 'μῆνις'
curlemma = 'ἔχω'
#curlemma = 'πέμπω'

print(len(lemmaindex[curlemma]))
deptot = 0
for foo in sorted(worddeprels[curlemma],key=worddeprels[curlemma].get,reverse=True):
    deptot = deptot + worddeprels[curlemma][foo]
    print(foo,worddeprels[curlemma][foo])
print(deptot,deptot/len(lemmaindex[curlemma]))

887
root 369
advcl 230
acl:relcl 111
amod 52
ccomp 35
acl:compl 26
orphan 15
nmod 9
nsubj 8
dislocated:obj 5
dislocated 5
acl 4
appos 3
xcomp 3
parataxis 3
advcl:compl 3
obj 3
vocative 1
csubj 1
obl 1
887 1.0


In [20]:
worddeprels['χόλος']

{'obj': 40, 'nsubj': 23, 'obl': 2, 'obl:arg': 1, 'amod': 1}

In [21]:
re.search('\\bobj','obj')

<re.Match object; span=(0, 3), match='obj'>

In [28]:
lemmaindex['μιμνάζω']

['tlg0012.tlg001:sent-2274673:9', 'tlg0012.tlg001:sent-2277438:9']

In [9]:
formindex['ἦλφον']

['tlg0012.tlg001:sent-2280967:33']